In [2]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline


In [3]:
"""
AdaptiveForecaster - A flexible class for time series forecasting with sktime
"""
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from typing import List, Union, Dict, Any, Optional, Tuple

from sktime.forecasting.model_selection import (
    ForecastingGridSearchCV, 
    temporal_train_test_split
)
from sktime.split import (
    ExpandingWindowSplitter, 
    SlidingWindowSplitter,
    TemporalTrainTestSplitter
)
from sktime.performance_metrics.forecasting import (
    MeanAbsolutePercentageError, 
    MeanSquaredError,
    MeanAbsoluteError
)

# Import our models factory
from models import get_forecaster, ALGORITHM_MAP

class AdaptiveForecaster:
    """
    A flexible class for time series forecasting that allows users to:
    - Choose from various forecasting algorithms
    - Apply different cross-validation strategies
    - Select performance metrics
    - Fit, predict and evaluate models
    - Visualize results
    
    This class wraps around the forecaster factory in models.py
    """
    
    def __init__(
        self,
        algorithm: str = 'arima',
        seasonal_period: int = 12,
        fh: Union[int, List[int]] = 3,
        cv_strategy: str = 'expanding',
        cv_window_length: int = 12,
        cv_step_length: int = 1,
        cv_initial_window: int = 24,
        test_size: float = 0.2,
        metric: str = 'rmse',
        n_jobs: int = -1,
        verbose: int = 1
    ):
        """
        Initialize the AdaptiveForecaster.
        
        Parameters
        ----------
        algorithm : str, default='arima'
            Name of the forecasting algorithm to use. Must be a key in ALGORITHM_MAP.
        seasonal_period : int, default=12
            The seasonal period of the time series.
        fh : int or list of ints, default=3
            The forecast horizon.
        cv_strategy : str, default='expanding'
            The cross-validation strategy to use. 
            Options: 'expanding', 'sliding', 'temporal'.
        cv_window_length : int, default=12
            The length of the window for cross-validation.
        cv_step_length : int, default=1
            The step length for sliding and expanding window cross-validation.
        cv_initial_window : int, default=24
            The initial window size for expanding window cross-validation.
        test_size : float, default=0.2
            The proportion of the dataset to include in the test split when using
            temporal_train_test_split.
        metric : str, default='rmse'
            The performance metric to use. 
            Options: 'rmse', 'mse', 'mae', 'mape'.
        n_jobs : int, default=-1
            The number of jobs to run in parallel.
        verbose : int, default=1
            The verbosity level.
        """
        # Validate algorithm
        if algorithm not in ALGORITHM_MAP:
            raise ValueError(f"Unknown algorithm: {algorithm}. Available: {list(ALGORITHM_MAP.keys())}")
        
        self.algorithm = algorithm
        self.seasonal_period = seasonal_period
        self.fh = fh
        self.cv_strategy = cv_strategy
        self.cv_window_length = cv_window_length
        self.cv_step_length = cv_step_length
        self.cv_initial_window = cv_initial_window
        self.test_size = test_size
        self.metric_name = metric
        self.n_jobs = n_jobs
        self.verbose = verbose
        
        # Initialize attributes that will be set later
        self.forecaster = None
        self.cv_splitter = None
        self.grid_search = None
        self.best_params = None
        self.best_score = None
        self.predictions = None
        self.prediction_intervals = None
        self.train_y = None
        self.test_y = None
        self.metric_func = None
        self.test_score = None
        
        # Set up the forecaster and cross-validation
        self._setup_forecaster()
        self._setup_metric()
    
    def _setup_forecaster(self):
        """Set up the forecaster using models.py factory function."""
        self.forecaster = get_forecaster(
            algorithm=self.algorithm,
            seasonal_period=self.seasonal_period
        )
    
    def _setup_metric(self):
        """Set up the performance metric function."""
        self.metrics_map = {
            'rmse': MeanSquaredError(square_root=True),
            'mse': MeanSquaredError(square_root=False),
            'mae': MeanAbsoluteError(),
            'mape': MeanAbsolutePercentageError()
        }
        
        if self.metric_name not in self.metrics_map:
            raise ValueError(f"Unknown metric: {self.metric_name}. Available: {list(self.metrics_map.keys())}")
        
        self.metric_func = self.metrics_map[self.metric_name]
    
    def _setup_cv_splitter(self, y=None):
        """Set up the cross-validation splitter based on cv_strategy."""
        if self.cv_strategy == 'expanding':
            self.cv_splitter = ExpandingWindowSplitter(
                initial_window=self.cv_initial_window,
                step_length=self.cv_step_length,
                fh=self.fh
            )
        elif self.cv_strategy == 'sliding':
            self.cv_splitter = SlidingWindowSplitter(
                window_length=self.cv_window_length,
                step_length=self.cv_step_length,
                fh=self.fh
            )
        elif self.cv_strategy == 'temporal':
            if y is None:
                raise ValueError("For temporal CV, y must be provided at initialization")
            self.cv_splitter = TemporalTrainTestSplitter(
                test_size=self.test_size
            )
        else:
            raise ValueError(f"Unknown CV strategy: {self.cv_strategy}. "
                             f"Available: ['expanding', 'sliding', 'temporal']")
    
    def setup_grid_search(self, y=None, param_grid=None):
        """
        Set up the grid search cross-validation.
        
        Parameters
        ----------
        y : pd.Series, optional
            The time series data. Required for temporal CV.
        param_grid : dict, optional
            The parameter grid for grid search. If None, uses the default from the forecaster.
        """
        self._setup_cv_splitter(y)
        
        if param_grid is None:
            param_grid = self.forecaster.get_param_grid()
        
        self.grid_search = ForecastingGridSearchCV(
            forecaster=self.forecaster.permuted,
            param_grid=param_grid,
            cv=self.cv_splitter,
            scoring=self.metric_func,
            n_jobs=self.n_jobs,
            verbose=self.verbose
        )
        
        return self
    
    def split_data(self, y, test_size=None):
        """
        Split the data into training and test sets.
        
        Parameters
        ----------
        y : pd.Series
            The time series data.
        test_size : float, optional
            The proportion of the dataset to include in the test split.
            If None, uses the value from initialization.
        
        Returns
        -------
        train_y, test_y : pd.Series
            The training and test data.
        """
        if test_size is None:
            test_size = self.test_size
        
        self.train_y, self.test_y = temporal_train_test_split(y, test_size=test_size)
        return self.train_y, self.test_y
    
    def fit(self, y, X=None, fh=None, use_test_set=False):
        """
        Fit the forecaster to the training data.
        
        Parameters
        ----------
        y : pd.Series
            The time series data.
        X : pd.DataFrame, optional
            Exogenous variables.
        fh : int or list of ints, optional
            The forecast horizon. If None, uses the value from initialization.
        use_test_set : bool, default=False
            Whether to split the data into train/test sets for final evaluation.
            If True, y is split internally and only the training portion is used for fitting.
        
        Returns
        -------
        self : AdaptiveForecaster
            The fitted forecaster.
        """
        if fh is not None:
            self.fh = fh
        
        # Handle train/test split if requested
        if use_test_set and self.train_y is None:
            print("Splitting data into train/test sets...")
            self.train_y, self.test_y = self.split_data(y)
            # Use training data for fitting
            y_to_fit = self.train_y
        else:
            # Use all data for fitting
            y_to_fit = y
        
        if self.grid_search is None:
            self.setup_grid_search(y_to_fit)
        
        print(f"Fitting {self.algorithm} forecaster with {self.cv_strategy} cross-validation...")
        self.grid_search.fit(y_to_fit, X=X, fh=self.fh)
        
        self.best_params = self.grid_search.best_params_
        self.best_score = self.grid_search.best_score_
        
        return self
    
    def predict(self, fh=None, X=None, return_pred_int=False, coverage=[0.95]):
        """
        Make predictions with the fitted forecaster.
        
        Parameters
        ----------
        fh : int or list of ints, optional
            The forecast horizon. If None, uses the value from initialization.
        X : pd.DataFrame, optional
            Exogenous variables.
        return_pred_int : bool, default=False
            Whether to return prediction intervals.
        coverage : list of float, default=[0.95]
            The coverage of prediction intervals.
        
        Returns
        -------
        predictions : pd.Series
            The point forecasts.
        """
        if self.grid_search is None or not hasattr(self.grid_search, 'best_forecaster_'):
            raise ValueError("Forecaster has not been fitted yet. Call fit() first.")
        
        if fh is None:
            fh = self.fh
        
        print("Making predictions...")
        self.predictions = self.grid_search.best_forecaster_.predict(fh=fh, X=X)
        
        if return_pred_int:
            try:
                self.prediction_intervals = self.grid_search.best_forecaster_.predict_interval(
                    fh=fh, X=X, coverage=coverage
                )
            except Exception as e:
                print(f"Warning: Could not compute prediction intervals: {e}")
                self.prediction_intervals = None
        
        return self.predictions
    
    def evaluate(self, y_true=None, in_sample=False, metrics=None):
        """
        Evaluate the forecaster on test data or in-sample using multiple metrics.
        
        Parameters
        ----------
        y_true : pd.Series, optional
            The true values to compare against. If None, uses self.test_y or the training data.
        in_sample : bool, default=False
            Whether to evaluate on the training data (in-sample) instead of test data.
            If True and y_true is None, will use the training data.
        metrics : list of str, optional
            List of metric names to compute. If None, computes all available metrics.
            Available: 'rmse', 'mse', 'mae', 'mape'
        
        Returns
        -------
        scores : dict
            Dictionary with metric names as keys and scores as values.
        """
        if self.predictions is None:
            raise ValueError("No predictions available. Call predict() first.")
        
        if y_true is None:
            if in_sample:
                if self.train_y is not None:
                    y_true = self.train_y
                else:
                    raise ValueError("No training data available. Provide y_true or call split_data() first.")
            else:
                if self.test_y is not None:
                    y_true = self.test_y
                else:
                    raise ValueError("No test data available. Provide y_true, call split_data(), "
                                   "or set in_sample=True to evaluate on training data.")
        
        # Align indices for evaluation
        # Only use the indices that appear in both series
        common_indices = y_true.index.intersection(self.predictions.index)
        if len(common_indices) == 0:
            raise ValueError("No common indices between true values and predictions")
        
        y_true_aligned = y_true.loc[common_indices]
        predictions_aligned = self.predictions.loc[common_indices]
        
        # Determine which metrics to compute
        if metrics is None:
            metrics_to_compute = list(self.metrics_map.keys())
        else:
            invalid_metrics = [m for m in metrics if m not in self.metrics_map]
            if invalid_metrics:
                raise ValueError(f"Unknown metrics: {invalid_metrics}. Available: {list(self.metrics_map.keys())}")
            metrics_to_compute = metrics
        
        # Compute all requested metrics
        scores = {}
        for metric_name in metrics_to_compute:
            metric_func = self.metrics_map[metric_name]
            scores[metric_name] = metric_func(y_true_aligned, predictions_aligned)
        
        # Store the main metric score
        self.test_score = scores[self.metric_name]
        
        # Print results
        eval_type = "In-sample" if in_sample else "Test"
        print(f"\n{eval_type} Performance Metrics:")
        print("-" * 30)
        for metric_name, score in scores.items():
            print(f"{metric_name.upper()}: {score:.4f}")
        
        return scores
    
    def plot_forecasts(self, y=None, title=None, figsize=(15, 7), include_intervals=True):
        """
        Plot the time series, forecasts, and prediction intervals.
        
        Parameters
        ----------
        y : pd.Series, optional
            The full time series data. If None, uses the train and test data.
        title : str, optional
            The title of the plot.
        figsize : tuple, default=(15, 7)
            The figure size.
        include_intervals : bool, default=True
            Whether to include prediction intervals in the plot.
        
        Returns
        -------
        fig : matplotlib.figure.Figure
            The figure object.
        """
        if self.predictions is None:
            raise ValueError("No predictions available. Call predict() first.")
        
        plt.figure(figsize=figsize)
        
        # Plot historical data
        if y is not None:
            plt.plot(y.index, y, 'k-', label='Historical Data')
        else:
            if self.train_y is not None:
                plt.plot(self.train_y.index, self.train_y, 'k-', label='Training Data')
            if self.test_y is not None:
                plt.plot(self.test_y.index, self.test_y, 'b-', label='Test Data')
        
        # Plot predictions
        plt.plot(self.predictions.index, self.predictions, 'r-', 
                 label=f'{self.algorithm.capitalize()} Forecast')
        
        # Plot prediction intervals if available
        if include_intervals and self.prediction_intervals is not None:
            for coverage in self.prediction_intervals.index.get_level_values(0).unique():
                lower = self.prediction_intervals.loc[coverage]["lower"]
                upper = self.prediction_intervals.loc[coverage]["upper"]
                plt.fill_between(
                    lower.index, lower, upper, alpha=0.2, color='r',
                    label=f"{int(coverage*100)}% Prediction Interval"
                )
        
        # Set title and labels
        if title is None:
            title = f"{self.algorithm.capitalize()} Forecast with {self.cv_strategy.capitalize()} CV"
        plt.title(title)
        plt.xlabel('Time')
        plt.ylabel('Value')
        plt.legend()
        plt.grid(True)
        
        return plt.gcf()
    
    def summary(self, include_metrics=None):
        """
        Print a summary of the forecasting results.
        
        Parameters
        ----------
        include_metrics : list of str, optional
            List of metric names to include in summary. If None, includes the main metric.
            
        Returns
        -------
        summary_dict : dict
            A dictionary containing the summary information.
        """
        if self.grid_search is None or not hasattr(self.grid_search, 'best_forecaster_'):
            raise ValueError("Forecaster has not been fitted yet. Call fit() first.")
        
        # Compute additional metrics if requested
        all_metrics = {}
        if include_metrics and self.test_y is not None and self.predictions is not None:
            all_metrics = self.evaluate(metrics=include_metrics)
        
        summary_dict = {
            "Algorithm": self.algorithm,
            "CV Strategy": self.cv_strategy,
            "Primary Metric": self.metric_name.upper(),
            "CV Score": self.best_score,
            "Test Score": self.test_score if self.test_score is not None else "Not evaluated",
            "Best Parameters": self.best_params,
        }
        
        # Add other metrics if available
        for metric, score in all_metrics.items():
            if metric != self.metric_name:  # Skip primary metric as it's already included
                summary_dict[f"{metric.upper()} Score"] = score
        
        print("\n" + "="*50)
        print(f"ADAPTIVE FORECASTER SUMMARY")
        print("="*50)
        
        # Print algorithm and strategy first
        print(f"Algorithm: {summary_dict['Algorithm']}")
        print(f"CV Strategy: {summary_dict['CV Strategy']}")
        
        # Print metrics section
        print("\nMetrics:")
        print(f"  Primary ({summary_dict['Primary Metric']})")
        print(f"    CV: {summary_dict['CV Score']:.4f}")
        print(f"    Test: {summary_dict['Test Score'] if isinstance(summary_dict['Test Score'], str) else summary_dict['Test Score']:.4f}")
        
        # Print additional metrics if available
        for k, v in summary_dict.items():
            if k.endswith(' Score') and k not in ['CV Score', 'Test Score']:
                print(f"  {k}: {v:.4f}")
        
        # Print best parameters
        print("\nBest Parameters:")
        for param, value in summary_dict['Best Parameters'].items():
            print(f"  {param}: {value}")
        
        print("="*50 + "\n")
        
        return summary_dict

In [4]:
"""
Example showing how to evaluate forecasts with multiple metrics
"""
import pandas as pd
import matplotlib.pyplot as plt
from sktime.datasets import load_airline

#from adaptive_forecaster import AdaptiveForecaster

# Load example data
print("Loading airline passengers dataset...")
y = load_airline()

# Create forecaster with RMSE as the primary optimization metric
forecaster = AdaptiveForecaster(
    algorithm='exp_smoothing',
    seasonal_period=12,
    fh=6,
    cv_strategy='expanding',
    cv_initial_window=80,
    test_size=0.2,
    metric='rmse'  # Primary metric for optimization
)

# Split data, fit model, and make predictions
train_y, test_y = forecaster.split_data(y)

forecaster.fit(train_y)
"""
forecaster.predict()

# Evaluate with multiple metrics
print("\n=== Evaluating with Multiple Metrics ===")
all_metrics = forecaster.evaluate(metrics=['rmse', 'mse', 'mae', 'mape'])

print("\nNote that the model was optimized for RMSE during cross-validation,")
print("but we can evaluate its performance using multiple metrics.")

# Create a comprehensive summary that includes all metrics
print("\n=== Comprehensive Model Summary ===")
summary = forecaster.summary(include_metrics=['rmse', 'mse', 'mae', 'mape'])

# Plot the forecasts
fig = forecaster.plot_forecasts(y)
plt.tight_layout()
"""

Loading airline passengers dataset...
Fitting exp_smoothing forecaster with expanding cross-validation...
Fitting 30 folds for each of 144 candidates, totalling 4320 fits


/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/sktime/forecasting/model_selection/_tune.py:90: UserWarning: Parameter n_jobs of ForecastingGridSearchCV has been removed in sktime 0.27.0 and is no longer used. It is ignored when passed. Instead, the backend and backend_params parameters should be used to pass n_jobs or other parallelization parameters.
  warn(
/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/sktime/utils/parallel.py:92: FitFailedWarning: 
                In evaluate, fitting of forecaster Permute failed,
                you can set error_score='raise' in evaluate to see
                the exception message.
                Fit failed for the 0-th data split, on training data y_train with
                cutoff NaT, and len(y_train)=80.
                The score will be set to nan.
                Failed forecaster with parameters: Permute(estimator=TransformedTargetForecaster(steps=[(

'\nforecaster.predict()\n\n# Evaluate with multiple metrics\nprint("\n=== Evaluating with Multiple Metrics ===")\nall_metrics = forecaster.evaluate(metrics=[\'rmse\', \'mse\', \'mae\', \'mape\'])\n\nprint("\nNote that the model was optimized for RMSE during cross-validation,")\nprint("but we can evaluate its performance using multiple metrics.")\n\n# Create a comprehensive summary that includes all metrics\nprint("\n=== Comprehensive Model Summary ===")\nsummary = forecaster.summary(include_metrics=[\'rmse\', \'mse\', \'mae\', \'mape\'])\n\n# Plot the forecasts\nfig = forecaster.plot_forecasts(y)\nplt.tight_layout()\n'

In [ ]:
forecaster.predict()
print("\n=== Evaluating with Multiple Metrics ===")
all_metrics = forecaster.evaluate(metrics=['rmse', 'mse', 'mae', 'mape'])

print("\nNote that the model was optimized for RMSE during cross-validation,")
print("but we can evaluate its performance using multiple metrics.")

# Create a comprehensive summary that includes all metrics
print("\n=== Comprehensive Model Summary ===")
summary = forecaster.summary(include_metrics=['rmse', 'mse', 'mae', 'mape'])

# Plot the forecasts
fig = forecaster.plot_forecasts(y)
plt.tight_layout()

In [6]:
import warnings
import os
from sktime.datasets import load_airline
os.environ['PYTHONWARNINGS'] = 'ignore'
algorithms = ['arima', 'exp_smoothing', 'stats_arima', 'naive']
results = []
y = load_airline()
# Create a DataFrame to store all results
comparison_data = []

for algo in algorithms:
    print(f"\nTesting {algo}...")
    algo_forecaster = AdaptiveForecaster(
        algorithm=algo,
        seasonal_period=12, 
        fh=6,
        cv_strategy='expanding',
        cv_initial_window=80,
        cv_step_length=3,
        metric='rmse',  # All models optimize for RMSE
        verbose=0
    )
    
    try:
        # Split, fit, predict
        train_y, test_y = algo_forecaster.split_data(y)
        algo_forecaster.fit(train_y)
        algo_forecaster.predict()
        
        # Evaluate with all metrics
        metrics = algo_forecaster.evaluate(metrics=['rmse', 'mse', 'mae', 'mape'])
        
        # Add to comparison data
        comparison_data.append({
            'Algorithm': algo,
            'RMSE': metrics['rmse'],
            'MSE': metrics['mse'],
            'MAE': metrics['mae'],
            'MAPE': metrics['mape']
        })
    except Exception as e:
        print(f"Error with {algo}: {e}")

# Create comparison table
if comparison_data:
    comparison_df = pd.DataFrame(comparison_data)
    print("\n=== Algorithm Comparison ===")
    print(comparison_df.set_index('Algorithm'))
    
    # Find best algorithm for each metric
    print("\n=== Best Algorithm per Metric ===")
    for metric in ['RMSE', 'MSE', 'MAE', 'MAPE']:
        best_algo = comparison_df.loc[comparison_df[metric].idxmin()]
        print(f"Best for {metric}: {best_algo['Algorithm']} ({best_algo[metric]:.4f})")


Testing arima...
Fitting arima forecaster with expanding cross-validation...


/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/sktime/forecasting/model_selection/_tune.py:90: UserWarning: Parameter n_jobs of ForecastingGridSearchCV has been removed in sktime 0.27.0 and is no longer used. It is ignored when passed. Instead, the backend and backend_params parameters should be used to pass n_jobs or other parallelization parameters.
  warn(
/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/home/yaeg/Documents/projects/packages/Adaptive_

Making predictions...

Test Performance Metrics:
------------------------------
RMSE: 12.7267
MSE: 161.9690
MAE: 12.7267
MAPE: 0.0354

Testing exp_smoothing...
Fitting exp_smoothing forecaster with expanding cross-validation...
Making predictions...

Test Performance Metrics:
------------------------------
RMSE: 14.4468
MSE: 208.7088
MAE: 14.4468
MAPE: 0.0401

Testing stats_arima...
Fitting stats_arima forecaster with expanding cross-validation...


/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/sktime/forecasting/model_selection/_tune.py:90: UserWarning: Parameter n_jobs of ForecastingGridSearchCV has been removed in sktime 0.27.0 and is no longer used. It is ignored when passed. Instead, the backend and backend_params parameters should be used to pass n_jobs or other parallelization parameters.
  warn(
/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/statsforecast/arima.py:479: UserWarning: possible convergence problem: minimize gave code 2]
  warnings.warn(
/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/statsforecast/arima.py:479: UserWarning: possible convergence problem: minimize gave code 2]
  warnings.warn(
/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/statsforecast/arima.py:479: UserWarning: possible convergence problem: minimize gave code 2]
  warnin

Making predictions...

Test Performance Metrics:
------------------------------
RMSE: 17.5300
MSE: 307.3016
MAE: 17.5300
MAPE: 0.0487

Testing naive...
Fitting naive forecaster with expanding cross-validation...
Making predictions...

Test Performance Metrics:
------------------------------
RMSE: 10.1629
MSE: 103.2838
MAE: 10.1629
MAPE: 0.0282

=== Algorithm Comparison ===
                    RMSE         MSE        MAE      MAPE
Algorithm                                                
arima          12.726703  161.968964  12.726703  0.035352
exp_smoothing  14.446757  208.708789  14.446757  0.040130
stats_arima    17.530021  307.301632  17.530021  0.048695
naive          10.162866  103.283844  10.162866  0.028230

=== Best Algorithm per Metric ===
Best for RMSE: naive (10.1629)
Best for MSE: naive (103.2838)
Best for MAE: naive (10.1629)
Best for MAPE: naive (0.0282)


In [13]:
cv = ExpandingWindowSplitter(
    initial_window=86,  # 2 years of monthly data
    step_length=3,      # move forward 1 month each time
)
test_grid = {'estimator__deseasonalizer__passthrough': [True],
 'estimator__detrender__passthrough': [False],
 'estimator__forecaster__sp': [12],
 'estimator__forecaster__strategy': ['last'],
 'estimator__forecaster__window_length': [None],
 'estimator__scaler__passthrough': [True]}
dummy = ForecastingGridSearchCV(
            forecaster=algo_forecaster.grid_search.best_forecaster_,
            param_grid=test_grid,
            cv=cv,
            scoring=MeanSquaredError(square_root=True),
            n_jobs=-1
        )

dummy.fit(y)
#algo_forecaster.grid_search.best_forecaster_

/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/sktime/forecasting/model_selection/_tune.py:90: UserWarning: Parameter n_jobs of ForecastingGridSearchCV has been removed in sktime 0.27.0 and is no longer used. It is ignored when passed. Instead, the backend and backend_params parameters should be used to pass n_jobs or other parallelization parameters.
  warn(


ForecastingGridSearchCV(cv=ExpandingWindowSplitter(initial_window=86,
                                                   step_length=3),
                        forecaster=Permute(estimator=TransformedTargetForecaster(steps=[('detrender',
                                                                                         OptionalPassthrough(transformer=Detrender())),
                                                                                        ('deseasonalizer',
                                                                                         OptionalPassthrough(passthrough=True,
                                                                                                             transformer=Deseasonalizer(sp=12))),
                                                                                        ('scaler',
                                                                                         OptionalPassthrough(passthrough=True,
                                                                                                             trans...
                                                                                        ('forecaster',
                                                                                         NaiveForecaster(sp=12))])),
                        n_jobs=-1,
                        param_grid={'estimator__deseasonalizer__passthrough': [True],
                                    'estimator__detrender__passthrough': [False],
                                    'estimator__forecaster__sp': [12],
                                    'estimator__forecaster__strategy': ['last'],
                                    'estimator__forecaster__window_length': [None],
                                    'estimator__scaler__passthrough': [True]},
                        scoring=MeanSquaredError(square_root=True))

In [16]:
dummy.predict(fh=[1,2,3,4,5,6])

1961-01    448.886207
1961-02    422.886207
1961-03    450.886207
1961-04    492.886207
1961-05    503.886207
1961-06    566.886207
Freq: M, Name: Number of airline passengers, dtype: float64

In [17]:
from datetime import datetime
def store_results(algorithm, forecaster, predictions, test_results, future_predictions, model_info=None,results_storage=None):
    """
    Store forecasting results in memory for later use
    
    Parameters
    ----------
    algorithm : str
        Name of the algorithm
    forecaster : AdaptiveForecaster
        The fitted forecaster
    predictions : pd.Series
        Predictions for the test period
    test_results : dict
        Evaluation metrics on test data
    future_predictions : pd.Series
        Predictions for the future 12 months
    model_info : dict, optional
        Additional model information
        
    Returns
    -------
    result_id : str
        Unique identifier for the stored result
    """
    timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
    result_id = f"{algorithm}_{timestamp}"
    
    # Base result dictionary
    result = {
        "id": result_id,
        "algorithm": algorithm,
        "timestamp": datetime.now().isoformat(),
        "metrics": test_results,
        "best_params": forecaster.best_params,
        "cv_score": float(forecaster.best_score),
        "model_info": model_info or {},
        "series_info": {
            "name": "airline_passengers",
            "frequency": str(y.index.freq),
            "start_date": y.index.min().strftime("%Y-%m-%d"),
            "end_date": y.index.max().strftime("%Y-%m-%d"),
            "n_observations": len(y)
        },
        "forecaster": forecaster  # Store the actual forecaster object
    }
    
    # Store in the dictionary
    results_storage["models"][result_id] = result
    
    # Store the actual predictions
    if predictions is not None:
        results_storage["test_predictions"][result_id] = predictions
    
    if future_predictions is not None:
        results_storage["future_predictions"][result_id] = future_predictions
    
    print(f"Stored results for {algorithm} as {result_id}")
    
    return result_id,results_storage

In [21]:

# Compare different algorithms with multiple metrics
print("\n=== Comparing Different Algorithms with Multiple Metrics ===")
algorithms = ['arima', 'exp_smoothing', 'stats_arima', 'naive']
results_storage = {
    "models": {},            # Store model metadata
    "test_predictions": {},  # Store test period predictions
    "future_predictions": {} # Store future predictions
}
model_results = {}
comparison_data = []

for algo in algorithms:
    print(f"\nTesting {algo}...")
    
    try:
        # Create forecaster with proper test period horizon
        algo_forecaster = AdaptiveForecaster(
            algorithm=algo,
            seasonal_period=12,
            fh=6,  # Match test set length
            cv_strategy='expanding',
            cv_initial_window=36,
            test_size=0.2,
            metric='rmse',
            verbose=1
        )
        
        # Split, fit, predict
        train_y, test_y = algo_forecaster.split_data(y)
        algo_forecaster.fit(train_y)
        
        # Generate predictions for test period
        test_predictions = algo_forecaster.predict()
        
        # Evaluate with multiple metrics
        test_metrics = algo_forecaster.evaluate(metrics=['rmse', 'mape', 'mae', 'mse'])
        
        # Now generate future predictions (next 12 months after the end of the dataset)
        # First, we need to fit on the full dataset
        full_forecaster = AdaptiveForecaster(
            algorithm=algo,
            seasonal_period=12,
            fh=6,  # 12 months into the future
            cv_strategy='expanding',
            cv_initial_window=36,
            metric='rmse',
            verbose=0
        )
        
        # Fit on the full dataset
        full_forecaster.fit(y)
        
        # Generate future predictions
        future_fh = list(range(1, 13))  # Next 12 months
        future_predictions = full_forecaster.predict(fh=future_fh)
        
        # Store results in memory
        model_info = {
            "cv_strategy": algo_forecaster.cv_strategy,
            "seasonal_period": algo_forecaster.seasonal_period,
            "training_time": "N/A",  # Could add timing information
        }
        
        result_id,results_storage = store_results(
            algorithm=algo,
            forecaster=algo_forecaster,
            predictions=test_predictions,
            test_results=test_metrics,
            future_predictions=future_predictions,
            model_info=model_info,
            results_storage=results_storage
        )
        
        # Save the model result for later reference
        model_results[algo] = {
            "result_id": result_id,
            "forecaster": algo_forecaster,
            "full_forecaster": full_forecaster,
            "test_predictions": test_predictions,
            "future_predictions": future_predictions,
            "metrics": test_metrics
        }
        
        # Add to comparison table
        comparison_data.append({
            'Algorithm': algo,
            'Result ID': result_id,
            'RMSE': test_metrics['rmse'],
            'MAPE': test_metrics['mape'],
            'MAE': test_metrics['mae'],
            'MSE': test_metrics['mse']
        })
        
    except Exception as e:
        print(f"Error with {algo}: {e}")

# Create a comprehensive comparison table
if comparison_data:
    comparison_df = pd.DataFrame(comparison_data)
    
    print("\n=== Algorithm Comparison ===")
    print(comparison_df[['Algorithm', 'RMSE', 'MAPE', 'MAE']].set_index('Algorithm'))
    
    # Find best algorithm for each metric
    print("\n=== Best Algorithm per Metric ===")
    metrics = ['RMSE', 'MAPE', 'MAE', 'MSE']
    best_algorithms = {}
    
    for metric in metrics:
        best_algo_idx = comparison_df[metric].idxmin()
        best_algo = comparison_df.loc[best_algo_idx]
        best_algorithms[metric] = best_algo['Algorithm']
        print(f"Best for {metric}: {best_algo['Algorithm']} ({best_algo[metric]:.4f})")

/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/home/yaeg/Documents/projects/packages/Adaptive_forecast/.venv/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed 

KeyboardInterrupt: 